<center><br><br>
    TANF Data Collaborative <br>
    Applied Data Analytics Training | Spring 2022
    <h1> Checkpoint Notebook: TANF Enterers</h1>
    <span style="font-size: 1.5em;">
        <a href='https://www.coleridgeinitiative.org'>Coleridge Initiative</a>
    </span>
    <center>Maryah Garner, Rukhshan Arif Mian</center>

</center>

***Please work on this checkpoints notebook if you used TANF enterers (**tanf_start = 1**) to define your cohort in*** `02_Creating_a_cohort.ipynb`.

This notebook serves as an overview of what was discussed in `Linkage_and_Longitudinal_Analysis.ipynb` through **5 checkpoints**. 

At each checkpoint you will be replacing the `___` with the appropriate variable, function or R code snippet. 

Participants are encouraged to attempt the checkpoints on their own. Having said that, hints and suggested solutions are provided and these can be accessed by utilizing the following code:

Hints: `check_#.hint()`

Solutions: `check_#.solution()` – your solutions may vary based on how you define your cohort and the name of your cohort table. We have shared our suggested solutions.

In both cases, # refers to the checkpoint number. For example: we can access the hint and solution for Checkpoint 2 using: `check_2.hint()` and `check_2.solution` respectively. Note: Codes for accessing hints and solutions are currently commented out – in order for these to run, we would need to uncomment them first. 

**The purpose of this notebook and all other checkpoint notebooks is to get you to practice making changes to the code that will help construct your own research project. We have given hints and solutions but these are more applicable to a generic research project. You are encouraged to think about how these checkpoints, hints/solutions may help formulate and address your research question.**

In [ ]:
# Switching off warnings
options(warn = -1)

# Database interaction imports
suppressMessages(library(odbc))

# for data manipulation/visualization
suppressMessages(library(tidyverse))

# scaling data, calculating percentages, overriding default graphing
suppressMessages(library(scales))

#Switching on warnings
options(warn = 0)

source("03_Linkage_and_Longitudinal_Analysis_hints_solutions_Enterers.txt") # defining hints + solutions

In [ ]:
# Connect to the database
con <- DBI::dbConnect(odbc::odbc(),
                     Driver = "SQL Server",
                     Server = "msssql01.c7bdq4o2yhxo.us-gov-west-1.rds.amazonaws.com",
                     Trusted_Connection = "True")

<font color='red'>
Within `03_Linkage_and_Longitudinal_Analysis.ipynb`, we focused on looking at employment outcomes for TANF recipients who exited during the second quarter of 2018. This checkpoint takes a slightly different approach. Here, we aim to look at TANF experience and certain factors leading up to it. 

If you selected **tanf_start == 1** in `02_Creating_a_cohort.ipynb`, we encourage you to go through this notebook to understand how you can perform descriptive statistics to understand a recipient's TANF experience. 
</font> 

Through this checkpoints notebook you will work on:
1. Reading in all instances of when a recipient starts TANF (accounting for multiple spells)
2. Creating variables that indicate if a TANF recipient has multiple spells on TANF
3. Linking to wage records to create a linked-cohort
4. Counting the number of quarters employed in the 1 year (last 4 quarters) leading upto the TANF start date

## Checkpoint 1: Reading Cohort

To start off, we will combine the enterer cohort that you created in **02_Creating_a_cohort_checkpoints.ipynb** with the complete TANF cohort (**person_month_clean**). For your research project, you may be interested in having a dataframe that contains all TANF spells for an individual.

We ask you to make the following changes:
1. Fill in the first blank with the name of your cohort of TANF starters that you created in `02_Creating_a_cohort_checkpoints.ipynb`
2. Fill in the second blank to keep the year-quarter combination (format: 'YYYY Q#') that you used to create your cohort in `02_Creating_a_cohort_checkpoints.ipynb` :

In [ ]:
qry <- "SELECT pmc.*
FROM tr_tdc_2022.dbo.____ cts
JOIN tr_tdc_2022.dbo.person_month_clean pmc
ON cts.ssn = pmc.ssn
WHERE yr_quarter <= '____' AND pmc.tanf_start = 1"

cohort <- dbGetQuery(con, qry)

In [ ]:
# hint
check_1.hint()

In [ ]:
# solution
check_1.solution()

## Checkpoint 2: Number of Spells

One way to understand TANF experience is to check if a recipient has previously availed TANF. For your research project, you may be interested in looking at recipients who have no previous spells or some previous spells. You may also be interested in comparing TANF experiences for first time recipients with recipients who have appeared in TANF before. 

This checkpoint focuses on creating an indicator that allows us to see if a recipient has been on TANF before. For this purpose, we would want to group by an individual and count the number of times they appear in our joined cohort. If this value is 1, this means this is a recipient's first spell. However, if their value is > 1, this means that they have availed TANF before. 

Fill in the blank below to group by a recipient. Think about what variable we can use that can help us group by an individual. 

In [ ]:
cohort_spells <- cohort %>% 
    # fill in the blank below
    group_by(___) %>% 
    summarise(count_spells = n()) %>%
    mutate(in_tanf_before = ifelse(count_spells > 1, 'Yes', 'No'))

Next, we look at the count and proportion of TANF recipients who previous TANF spells. 

In [ ]:
# getting the count and proportion for each category within in_tanf_before
# no updates required
cohort_spells %>% 
    group_by(in_tanf_before) %>% 
    summarise(count = n()) %>%
    mutate(prop = count/sum(count))

In [ ]:
# hint
check_2.hint()

In [ ]:
# solution
check_2.solution()

## Checkpoint 3: Number of months in previous spells

To build on the previous checkpoint, we ask you to to group by the variable indicating if a recipient has multiple spells in TANF and calculate the average and median number of months (across all spells). 

Fill in the blank below to group by the variable that indicates if someone has multiple spells in TANF. 

In [ ]:
cohort_spells %>% 
    # joining with the cohort
    inner_join(cohort, by='ssn') %>% 
    # sorting by ssn and yr_month in descending order to keep latest value
    arrange(ssn, desc(yr_month)) %>%
    # dropping duplicates
    distinct(ssn, .keep_all=T) %>%
    # fill in the blank below with the variable that tells us if a respondent has multiple tanf spells
    group_by(___) %>%
    # counting the number of individuals in each category, calculating the mean and median for total_tanf_months
    summarise(count_individuals = n(), 
              average_months = mean(tanf_total_months), 
              median_months = median(tanf_total_months))

In [ ]:
# hint
check_3.hint()

In [ ]:
# solution
check_3.solution()

## Linking cohort to wage records: For first time TANF recipients

In the Exiters notebook, we are focusing on analyzing the post-TANF outcomes of adult individuals (age > 18). Since you are looking at Enterers, you may be interested in focusing on a TANF family as opposed to an individual. The next 2 checkpoints look at factors leading up to TANF entry for a TANF case (family) as opposed to a single recipient.

One such factor could be their employment in the past year and we can understand this by utilizing Indiana's wage records. To start off, we keep recipients who appeared in TANF for the first time on the start date (quarter) of your choice (defined in Checkpoint 1 and in `02_Creating_a_cohort_checkpoints.ipynb`). For the next set of checkpoints, we consider cases where **in_tanf_before == No** – as we are only interested in looking at first time TANF recipients. 

> Note: Since we are hoping to look at a TANF family as opposed to an individual, we will end up utilizing **caseid** as opposed to **ssn**. However, we do this in Checkpoint 5 – once we have brought in the wage data.

In [ ]:
# no update required
first_time_tanf <- cohort_spells %>% 
    filter(in_tanf_before == "No") %>% 
    inner_join(cohort, by="ssn") %>% 
    arrange(ssn, desc(yr_month)) %>%
    distinct(ssn, .keep_all=T) %>%
    select(ssn)

## Checkpoint 4: Linking cohort to wage records

Next, we ask you to update the code below based on the year-quarter (format: 'YYYY Q#'. Example: '2017 Q2') of your choice (note: this has to be in line with what you chose when creating your cohort in `02_Creating_a_cohort_checkpoints.ipynb`).

We ask you to look at employment uptil **one year** before a recipient entered TANF. That is, if someone entered TANF in the second quarter of 2017 (**yr_quarter = '2017 Q2'**), we would want to keep wage records between (but not inclusive of) **yr_quarter = '2016 Q1'** and **yr_quarter = '2017 Q2'** (note: your choice of years might be different).

For your research project, you may be interested in looking at wages or employment that spans more than (or less than) 4 pre-TANF quarters. This is one example of looking at circumstances leading upto TANF entry. 

We ask you to make the following changes:
1. Update the first blank with the name of your cohort (this is the same as the first blank from Checkpoint 1).
2. Update line 6 with the range of quarters of your choice. You may choose as many or as few quarters as you like.
3. Update the last blank with the name of your cohort (same as Checkpoint 1 and first blank in this checkpoint).

In [ ]:
qry <- "SELECT nb.*, wr.Empr_no, wr.Wage, wr.yr_quarter
    FROM (tr_tdc_2022.dbo.____ nb
    LEFT JOIN 
    (SELECT SSN, Empr_no, yr_quarter, Wage 
    FROM tr_tdc_2022.dbo.wages_tanf
    WHERE yr_quarter IN ('___', '___','___', '___')
    AND (SSN IN (SELECT DISTINCT SSN FROM tr_tdc_2022.dbo.____))) wr
    ON wr.SSN=nb.SSN)"

cohort_wages <- dbGetQuery(con, qry)


In [ ]:
# joining with the first_time_tanf dataframe to only keep wages for first_time_tanf_recipients
# no update required
cohort_wages_first_tanf <- cohort_wages %>% 
    right_join(first_time_tanf, by='ssn')

In [ ]:
# hint
check_4.hint()

In [ ]:
# solution
check_4.solution()

## Checkpoint 5: Number of Quarters employed Pre-TANF
Next, we ask you to fill in the blank below to get the total wages by each **caseid** in each quarter. We use **caseid** here because our goal is to look at the pre-TANF employment for a TANF family as opposed to a recipient. As a reminder, missing wages for a **caseid** in a given quarter implies no employment for anyone within the family receiving TANF. 

Fill in the blank below with the variable associated with wages. 

In [ ]:
tot_wages <- cohort_wages_first_tanf %>% 
    group_by(caseid, yr_quarter) %>% 
    # fill in the blank below with the variable associated with wages
    summarise(totalwages=sum(___))

In [ ]:
# number of quarters employed pre-TANF
tot_q_emp <- tot_wages %>% 
    group_by(caseid) %>%
    summarise(quarters_employed = sum(!is.na(totalwages)))

# number of quarters employed across TANF families in the year (4 quarters) leading upto TANF entry
tot_q_emp %>%
    group_by(quarters_employed) %>%
    summarise(count_cases=n())

In [ ]:
# hint
check_5.hint()

In [ ]:
check_5.solution()